
#OBJETIVO

O objetivo principal desse notebook é transformar os dados brutos do datasus.

_The primary objective of this notebook is to transform the DATASUS SIM raw data._


#Conectando ao ADLS Gen2

O Azure Key Vault foi utilizado como repositório para o token SAS do container ADLS datasus-data. Para realizar o acesso ao container, foi necessário configurar o Databricks Secret Scopes.

_Azure Key Vault served as the repository for the datadus-data ADLS container's SAS token. Databricks secret scopes were employed to get the SAS token and retrieve the raw data._


In [0]:
storage_account = 'coutjdatasusstorage'
container_name = 'datasus-data'

spark.conf.set(f"fs.azure.account.auth.type.{storage_account}.dfs.core.windows.net", "SAS")
spark.conf.set(f"fs.azure.sas.token.provider.type.{storage_account}.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.sas.FixedSASTokenProvider")
spark.conf.set(f"fs.azure.sas.fixed.token.{storage_account}.dfs.core.windows.net", dbutils.secrets.get(scope="adls_secrete", key="databricks-sas"))
# dbutils.secrets.list("adls_secrete")

conn_string = f"abfss://{container_name}@{storage_account}.dfs.core.windows.net/raw"


In [0]:
#Importing libs

import pyspark.sql.functions as f
from datetime import datetime
from pyspark.sql.types import TimestampType
from dateutil.relativedelta import relativedelta
from pathlib import Path

In [0]:
#READING datasus raw data parquet

# dbutils.fs.ls(conn_string)
dbutils.widgets.text("dir_name", "", "Enter dir_name")
dir_name = dbutils.widgets.get('dir_name') or 'DORJ2020.parquet'
print(dir_name)
df_datasus = spark.read.parquet(f"{conn_string}/{dir_name}")

DORJ2020.parquet


####TIPOBITO

Tipo do óbito

_Type of death_

TIPOBITO:
  * 1: óbito fetal
  * 2: óbito não fetal

In [0]:
df_datasus = df_datasus.withColumn('TIPOBITO', f.when(df_datasus.TIPOBITO == "1", 'FETAL')
                                 .otherwise('NAO FETAL')
                                 )



#####DTHORAOBITO

Data e hora do óbito, obtido a partir das colunas DTOBITO e HORAOBITO

_Date and time of death, obtained from the columns DTOBITO and HORAOBITO._


In [0]:
@udf(TimestampType())
def transform_data_hora(data, hora):
    data = data.strip()
    hora = hora.strip()

    if len(data) == 8 and len(hora) != 4:
        return  datetime.strptime(data, '%d%m%Y')
    elif len(data) == 8 and len(hora) == 4:
        data_hora = f"{data} {hora}"
        return datetime.strptime(data_hora, '%d%m%Y %H%M')
    else:
        return None

df_datasus = df_datasus.withColumn('DTHORAOBITO', transform_data_hora(df_datasus.DTOBITO, df_datasus.HORAOBITO))
df_datasus = df_datasus.drop(df_datasus.DTOBITO)
df_datasus = df_datasus.drop(df_datasus.HORAOBITO)

#####UFNATU e NOMEMUNNATU

SIGLA da UF e município de naturalidade do falecido.

_Abbreviation of the state (UF) and municipality of the deceased's place of birth._

In [0]:
#retrieve files with city's names and codes

df_uf_municipio = spark.read.csv(f"{conn_string}/Utils/municipios.csv", header=True)
df_uf_municipio.createOrReplaceTempView('uf_codes')

df_uf_codes = spark.sql('''
                SELECT DISTINCT uf, uf_code, substring(municipio, 1, 6) as municipio, name from uf_codes
                ORDER BY uf_code, municipio
          ''')

In [0]:
df_datasus.createOrReplaceTempView('susdata')
df_uf_codes.createOrReplaceTempView('uf_codes')

df_datasus = spark.sql(
    """
        with municipio_uf as (
            select municipio, name, uf_code, uf from uf_codes
            where trim(municipio) <> ''
        )

        select susdata.*, municipio_uf.uf_code AS UFNATU, municipio_uf.name AS NOMEMUNNATU from susdata
        LEFT JOIN municipio_uf
        ON susdata.CODMUNNATU = CAST(municipio_uf.municipio AS NUMERIC)
    """

)


#####DTNASC e IDADE

Data de nascimento e idade do falecido.

_Date of birth and age of the deceased._

In [0]:
df_datasus = df_datasus.withColumn('DTNASC', f.to_date(df_datasus.DTNASC, 'ddMMyyyy'))
df_datasus = df_datasus.withColumn('IDADE', f.round(f.months_between(df_datasus.DTHORAOBITO, df_datasus.DTNASC)/12, 1))


#####SEXO

Sexo do falecido.

_Deceased's gender._

SEXO: 
  * 0: Ignorado
  * 1: Masculino
  * 2: Feminino

In [0]:
df_datasus.createOrReplaceTempView('susdata')

df_datasus = df_datasus.withColumn('SEXO', f.when(f.col('SEXO') == 1, "M")
                                    .when(f.col('SEXO') == 2, 'F')
                                    .otherwise('IGNORADO')
            )


#####RACACOR

Raça/Cor

_ethnicity_

RACACOR:
  * 1: Branca
  * 2: Preta
  * 3: Amarela
  * 4: Parda
  * 5: Indígena

In [0]:
df_datasus = df_datasus.withColumn('RACACOR', f.when(f.col('RACACOR') == 1, 'BRANCA')
                                        .when(f.col('RACACOR') == 2, 'PRETA')
                                        .when(f.col('RACACOR') == 3, 'AMARELA')
                                        .when(f.col('RACACOR') == 4, 'PARDA')
                                        .when(f.col('RACACOR') == 5, 'INDIGENA')
                                        .otherwise('NAO DECLARADO')
                )

#####ESTCIV

Estado civíl.

_Marital status_.

ESTCIV:
  * 1: Solteiro
  * 2: Casado
  * 3: Viúvo
  * 4: Separado judicialmente
  * 5: União consensual (versões anteriores)
  * 9: Ignorado

In [0]:
df_datasus = df_datasus.withColumn('ESTCIV', f.when(df_datasus.ESTCIV == 1, 'SOLTEIRO')
                                        .when(df_datasus.ESTCIV == 2, 'CASADO')
                                        .when(df_datasus.ESTCIV == 3, 'VIUVO')
                                        .when(df_datasus.ESTCIV == 4, 'SEPARADO')
                                        .when(df_datasus.ESTCIV == 5, 'UNIAO ESTAVEL')
                                        .otherwise('IGNORADO')
                )


##### ESC2010

Escolaridade.

_Educational level_.

ESC2010:
  0 – Sem escolaridade
  * 1 – FundamentalI (1a a 4a série)
  * 2 – Fundamental II (5a a 8a série)
  * 3 – Médio(antigo 2o Grau)
  * 4 – Superior incompleto
  * 5 – Superior completo
  * 9– Ignorado.

In [0]:
df_datasus = df_datasus.withColumn('ESC2010', f.when(df_datasus.ESC2010 == 0, 'SEM ESCOLARIDADE')
                                        .when(df_datasus.ESC2010 == 1, 'FUNDAMENTAL I')
                                        .when(df_datasus.ESC2010 == 2, 'FUNDAMENTAL II')
                                        .when(df_datasus.ESC2010 == 3, 'MEDIO')
                                        .when(df_datasus.ESC2010 == 4, 'SUPERIOR INCOMPLETO')
                                        .when(df_datasus.ESC2010 == 0, 'SUPERIOR COMPLETO')
                                        .otherwise('IGNORADO')
                )


#####OCUP

Ocupação

_Occupattion_

In [0]:
#retrieve file with occupation's names and codes


df_ocupacoes = spark.read.csv(
                                f"{conn_string}/Utils/CBO2002 - Ocupacao.csv",
                                header=True, 
                                encoding='ISO-8859-1',
                                sep=';'
                            )

In [0]:
df_ocupacoes.createOrReplaceTempView('ocupacoes')
df_datasus.createOrReplaceTempView('susdata')

df_datasus = spark.sql(
    """
        SELECT susdata.*, ocupacoes.TITULO as OCUPTITULO FROM susdata
        LEFT JOIN ocupacoes
        WHERE susdata.OCUP = ocupacoes.CODIGO
    """
)


#####NOMEMUNRES e UFRES

Nome do município e UF de residência.

_City name and state (UF) of residence._

In [0]:
df_datasus.createOrReplaceTempView('susdata')
df_uf_codes.createOrReplaceTempView('uf_codes')


df_datasus = spark.sql("""
                SELECT susdata.*, uf_codes.uf_code AS UFRES, uf_codes.name AS NOMEMUNRES FROM susdata
                LEFT JOIN uf_codes
                ON CAST(uf_codes.municipio AS NUMERIC) = susdata.CODMUNRES
          """)


#####LOCOCOR

Local de ocorrência do óbito.

_Place of death occurrence._

In [0]:
df_datasus = df_datasus.withColumn('LOCOCOR', f.when(df_datasus.LOCOCOR == 1, 'HOSPITAL')
                                        .when(df_datasus.LOCOCOR == 2, 'OUTROS ESTABELICIMENTOS DE SAUDE')
                                        .when(df_datasus.LOCOCOR == 3, 'DOMICILIO')
                                        .when(df_datasus.LOCOCOR == 4, 'VIA PUBLICA')
                                        .when(df_datasus.LOCOCOR == 5, 'OUTROS')
                                        .when(df_datasus.LOCOCOR == 6, 'ALDEIA INDIGENA')
                                        .otherwise('IGNORADO')                        
                )

#####CODMUNOCOR

Código do município de ocorrência.

_City of occurrence code._


In [0]:
df_datasus.createOrReplaceTempView('susdata')
df_uf_codes.createOrReplaceTempView('uf_codes')


df_datasus= spark.sql("""
                SELECT susdata.*, uf_codes.uf_code AS UFMUNOCOR, uf_codes.name AS NOMEMUNOCOR FROM susdata
                LEFT JOIN uf_codes
                ON CAST(uf_codes.municipio AS NUMERIC) = susdata.CODMUNOCOR
          """)


#####ASSISTMED

Indica se houve assistência médica.

_Indicates whether medical assistance was provided._

ASSISTMED:
  * 9: Ignorado
  * 1: Com assistência
  * 2: Sem assistência

In [0]:
df_datasus = df_datasus.withColumn('ASSISTMED', f.when(df_datasus.ASSISTMED == '1', 'SIM')
                                            .when(df_datasus.ASSISTMED == '2', 'NAO')
                                            .otherwise('IGNORADO')
                          )


#####NECROPSIA

Indica se houve necrópsia.

_Indicates whether there was a necropsy_

NECROPSIA:
  * 9: Ignorado
  * 1: Sim
  * 2: Não

In [0]:
df_datasus = df_datasus.withColumn('NECROPSIA', f.when(df_datasus.NECROPSIA == 1, 'SIM')
                                        .when(df_datasus.NECROPSIA == 2, 'NAO')
                                        .otherwise('IGNORADO')          
                )

#####CAUSABAS

Causa básica, conforme a Classificação Internacional de Doença (CID), 10a. Revisão

_Basic cause, according to the International Classification of Disease (ICD), 10a. Revision_

In [0]:
#retrieve files with disease's names and codes

df_cid10_sub = spark.read.csv(
                                f"{conn_string}/Utils/CID-10-SUBCATEGORIAS.CSV",
                                header=True, 
                                encoding='ISO-8859-1',
                                sep=';'
                            )

df_cid10_cat = spark.read.csv(
                                f"{conn_string}/Utils/CID-10-CATEGORIAS.CSV",
                                header=True, 
                                encoding='ISO-8859-1',
                                sep=';'
                            )

df_cid10_sub = df_cid10_sub.select(df_cid10_sub.SUBCAT, df_cid10_sub.DESCRICAO)
df_cid10_cat = df_cid10_cat.select(df_cid10_cat.CAT, df_cid10_cat.DESCRICAO)

In [0]:
df_cid10_sub.createOrReplaceTempView('cid10_sub')
df_datasus.createOrReplaceTempView('susdata')

df_datasus = spark.sql(
    """
        SELECT susdata.*, cid10_sub.DESCRICAO AS CAUSABASDESCSUBCAT FROM susdata
        LEFT JOIN cid10_sub
        ON susdata.CAUSABAS = cid10_sub.SUBCAT
    """
)


In [0]:
df_cid10_cat.createOrReplaceTempView('cid10_cat')
df_datasus.createOrReplaceTempView('susdata')

df_datasus = spark.sql(
    """
        SELECT susdata.*, cid10_cat.DESCRICAO AS CAUSABASDESCCAT FROM susdata
        LEFT JOIN cid10_cat
        ON SUBSTRING(susdata.CAUSABAS, 1, 3) = cid10_cat.CAT
    """
)



#####CIRCOBITO

Indica o tipo de acidente.

_Specifies the type of accident._

In [0]:
df_datasus = df_datasus.withColumn('CIRCOBITO', f.when(df_datasus.CIRCOBITO == 1, 'ACIDENTE')
                                            .when(df_datasus.CIRCOBITO == 2, 'SUICIDIO')
                                            .when(df_datasus.CIRCOBITO == 3, 'HOMICIDIO')
                                            .when(df_datasus.CIRCOBITO == 4, 'OUTROS')
                                            .otherwise('IGNORADO')              
            )


#####ACIDTRAB

Indica se foi acidente de trabalho.

_Specifies whether it was a work-related accident._

ACIDTRAB:
  * 9: Ignorado
  * 1: Sim
  * 2: Não

In [0]:
df_datasus = df_datasus.withColumn('ACIDTRAB', f.when(df_datasus.ACIDTRAB == 1, 'SIM')
                                        .when(df_datasus.ACIDTRAB == 2, 'NAO')
                                        .otherwise('IGNORADO')
                          )

#####TPPOS

Óbito investigado

_Death under investigation_

TPPOS:
  * 1: Sim
  * 2: Não

In [0]:
df_datasus = df_datasus.withColumn('TPPOS', f.when(df_datasus.TPPOS == 'S', 'SIM')
                                    .when(df_datasus.TPPOS == 'N', 'NAO')
                                    .otherwise('IGNORADO')
                          )

In [0]:
#DROP

# column_to_drop = ['CODESTAB', 'ESTABDESCR', 'OCUPMAE', 'GESTACAO', 'IDADEMAE', 'ESCMAE', 'ESCMAE2010', 'SERIESCMAE', 'QTDFILVIVO', 'QTDFILMORT',
#                 'GRAVIDEZ', 'SEMAGESTAC', 'PARTO', 'OBITOPARTO', 'PESO', 'TPMORTEOCO', 'OBITOGRAV', 'EXAME', 'CIRURGIA',
#                 'OBITOPUERP', 'LINHAA', 'LINHAB', 'LINHAC', 'LINHAD', 'LINHAII', 'CBPRE', 'DTATESTADO','COMUNSVOIM', 'FONTE', 'NUMEROLOTE',
#                 'DTINVESTIG', 'CAUSABAS_O', 'DTCADASTRO', 'ATESTANTE', 'STCODIFICA', 'CODIFICADO', 'VERSAOSIST', 'VERSAOSCB', 'FONTEINV',
#                 'DTRECEBIM', 'ATESTADO', 'DTRECORIGA', 'CAUSAMAT', 'ESCMAEAGR1', 'ESCFALAGR1', 'ESTATUSDOEPIDEM', 'STDONOVA', 'DIFDATA', 'NUDIASOBCO',
#                 'NUDIASOBIN', 'DTCADINV', 'TPOBITOCOR', 'DTCONINV', 'FONTES', 'TPRESGINFO', 'TPNIVELINV', 'NUDIASINF', 'DTCADINF', 'MORTEPARTO', 'DTCONCASO',
#                 'FONTESINF', 'ALTCAUSA', 'SERIESCFAL', 'CB_PRE', 'STDOEPIDEM', 'ESC']

# df_datasus = df_datasus.select([column for column in df_datasus.columns if column not in column_to_drop])
# display(df_datasus)

In [0]:
# df_datasus.columns

ordered_columns =  ['ORIGEM', 'TIPOBITO', 'DTHORAOBITO', 'NATURAL', 'UFNATU', 'CODMUNNATU', 'NOMEMUNNATU', 'DTNASC', 'IDADE', 'SEXO', 'RACACOR', 'ESTCIV', 'ESC2010', 'OCUP', 'OCUPTITULO', 'UFRES', 'CODMUNRES', 'NOMEMUNRES', 'LOCOCOR', 'UFMUNOCOR', 'CODMUNOCOR', 'NOMEMUNOCOR', 'ASSISTMED', 'NECROPSIA', 'CAUSABAS',  'CAUSABASDESCCAT', 'CAUSABASDESCSUBCAT', 'CIRCOBITO', 'ACIDTRAB', 'TPPOS', 'CONTADOR']

df = df_datasus.select([col for col in ordered_columns])

# display(df)

ORIGEM TIPOBITO DTHORAOBITO NATURAL UFNATU CODMUNNATU NOMEMUNNATU DTNASC IDADE SEXO RACACOR ESTCIV ESC2010 OCUP OCUPTITULO UFRES CODMUNRES NOMEMUNRES LOCOCOR UFMUNOCOR CODMUNOCOR NOMEMUNOCOR ASSISTMED NECROPSIA CAUSABAS CAUSABASDESCCAT CAUSABASDESCSUBCAT CIRCOBITO ACIDTRAB TPPOS CONTADOR 1 NAO FETAL 2021-06-21T09:00:00Z 833 RJ 330455 Rio de Janeiro 1958-05-14 63.1 M PRETA VIUVO IGNORADO 715210 Pedreiro RJ 330490 São Gonçalo DOMICILIO RJ 330490 São Gonçalo IGNORADO IGNORADO R99 Outras causas mal definidas e as não especificadas de mortalidade null IGNORADO IGNORADO NAO 917795 1 NAO FETAL 2021-06-07T23:55:00Z 833 RJ 330455 Rio de Janeiro 1976-05-13 45.1 F PARDA CASADO IGNORADO 262105 Produtor cultural RJ 330490 São Gonçalo HOSPITAL RJ 330330 Niterói SIM NAO C920 Leucemia mielóide Leucemia mielóide aguda IGNORADO IGNORADO NAO 917798 1 NAO FETAL 2021-06-19T15:00:00Z null null 1931-09-08 89.8 M BRANCA VIUVO FUNDAMENTAL I 711410 Operador de salina (sal marinho) RJ 330025 Arraial do Cabo HOSPITAL RJ 330025 Arraial do Cabo SIM NAO I132 Doença cardíaca e renal hipertensiva Doença cardíaca e renal hipertensiva com insuficiência cardíaca (congestiva) e insuficiência renal IGNORADO IGNORADO NAO 917802 1 NAO FETAL 2021-06-15T15:15:00Z 833 RJ 330455 Rio de Janeiro 1996-03-15 25.3 M PRETA SOLTEIRO FUNDAMENTAL II 524305 Vendedor ambulante RJ 330360 Paracambi HOSPITAL RJ 330620 Vassouras IGNORADO IGNORADO K746 Fibrose e cirrose hepáticas Outras formas de cirrose hepática e as não especificadas IGNORADO IGNORADO NAO 917857 1 NAO FETAL 2021-06-18T04:00:00Z 833 RJ 330455 Rio de Janeiro 1957-09-22 63.7 F BRANCA CASADO MEDIO 141410 Comerciante varejista RJ 330360 Paracambi HOSPITAL RJ 330455 Rio de Janeiro SIM NAO C269 Neoplasia maligna de outros órgãos digestivos e de localizações mal definidas no aparelho digestivo Neoplasia maligna de localizações mal definidas dentro do aparelho digestivo IGNORADO IGNORADO NAO 917858 1 NAO FETAL 2021-05-07T03:40:00Z 833 RJ 330500 São João da Barra 1951-11-26 69.4 M BRANCA CASADO FUNDAMENTAL II 354705 Representante comercial autônomo RJ 330475 São Francisco de Itabapoana HOSPITAL RJ 330100 Campos dos Goytacazes IGNORADO IGNORADO B342 Doenças por vírus, de localização não especificada Infecção por coronavírus de localização não especificada IGNORADO IGNORADO NAO 917875 1 NAO FETAL 2021-05-20T11:26:00Z 833 RJ 330010 Angra dos Reis 1994-06-09 26.9 M BRANCA SOLTEIRO MEDIO 141410 Comerciante varejista RJ 330010 Angra dos Reis DOMICILIO RJ 330010 Angra dos Reis NAO SIM X700 Lesão autoprovocada intencionalmente por enforcamento, estrangulamento e sufocação Lesão autoprovocada intencionalmente por enforcamento, estrangulamento e sufocação - residência SUICIDIO IGNORADO NAO 917901 1 NAO FETAL 2021-05-23T20:30:00Z 833 RJ 330030 Barra do Piraí 1948-03-20 73.2 F PRETA VIUVO FUNDAMENTAL I 513205 Cozinheiro geral RJ 330010 Angra dos Reis HOSPITAL RJ 330010 Angra dos Reis IGNORADO IGNORADO I619 Hemorragia intracerebral Hemorragia intracerebral não especificada IGNORADO IGNORADO NAO 917905 1 NAO FETAL 2021-06-19T13:00:00Z 825 PB 250380 Caldas Brandão 1980-02-09 41.4 M BRANCA SOLTEIRO SEM ESCOLARIDADE 513205 Cozinheiro geral RJ 330430 Rio Bonito HOSPITAL RJ 330455 Rio de Janeiro SIM NAO B342 Doenças por vírus, de localização não especificada Infecção por coronavírus de localização não especificada IGNORADO IGNORADO NAO 917968 1 NAO FETAL 2021-06-04T22:35:00Z 833 RJ 330455 Rio de Janeiro 1940-10-11 80.7 M BRANCA VIUVO IGNORADO 351810 Investigador de polícia RJ 330455 Rio de Janeiro HOSPITAL RJ 330455 Rio de Janeiro IGNORADO IGNORADO C189 Neoplasia maligna do cólon Neoplasia maligna do cólon, não especificado IGNORADO IGNORADO NAO 917970 1 NAO FETAL 2021-06-18T11:55:00Z 833 RJ 330455 Rio de Janeiro 1937-07-09 83.9 F BRANCA CASADO MEDIO 319110 Técnico em confecções do vestuário RJ 330455 Rio de Janeiro HOSPITAL RJ 330455 Rio de Janeiro IGNORADO IGNORADO B342 Doenças por vírus, de localização não especificada Infecção por coronavíru

In [0]:
trusted_file = str(Path(Path(conn_string).parent, 'trusted', 'name.parquet').absolute()).replace('/databricks/driver/', '')

mount_point = "/mnt/trusted"
config = {f'fs.azure.sas.{container_name}.{storage_account}.blob.core.windows.net': dbutils.secrets.get(scope="adls_secrete", key="databricks-sas")}

if not any(mount.mountPoint == mount_point for mount in dbutils.fs.mounts()):
  try:
    dbutils.fs.mount(
      source = "wasbs://{}@{}.blob.core.windows.net".format(container_name, storage_account),
      mount_point = mount_point,
      extra_configs = config
    )
    print("mount succeeded!")
  except Exception as e:
    print("mount exception", e)


df_datasus.write.parquet(f'/mnt/trusted/{dir_name}', mode='overwrite')